In [6]:
import numpy as np
from segment_anything import sam_model_registry, SamAutomaticMaskGenerator, SamPredictor
import glob
import cv2
import torch
from sklearn.cluster import KMeans
import os

In [2]:
a=[[1.7211274838128157, 8.922110963936303],[-1.2202704975818623, 3.351520923441087],[-6.604088344998228, -1.3005720637383407]]
a=np.array(a)
a.shape
a[:,0]-=3
a[:,1]+=3
a

array([[-1.27887252, 11.92211096],
       [-4.2202705 ,  6.35152092],
       [-9.60408834,  1.69942794]])

In [3]:
import json

def read_poses_from_json(file_path):
    """Reads the pose data from a JSON file."""
    with open(file_path, 'r') as file:
        data = json.load(file)
    return data

def write_matrices_to_txt(data, output_file_path):
    """Writes the 4x4 pose matrices to a text file."""
    if not os.path.exists(os.path.dirname(output_file_path)):
        os.makedirs(os.path.dirname(output_file_path))
    with open(output_file_path, 'w') as file:
        for frame_id, frame_data in data.items():
            pose = frame_data['pose']
            #file.write(f"{frame_id}:\n")
            for row in pose:
                formatted_row = ' '.join(f"{value:.18e}" for value in row)
                file.write(formatted_row + "\n")

def write_intirinsic_to_txt(data, output_file_path):
    """Writes the 4x4 pose matrices to a text file."""
    with open(output_file_path, 'w') as file:
        for frame_id, frame_data in data.items():
            pose = frame_data['intrinsic']
            #file.write(f"{frame_id}:\n")
            for row in pose:
                formatted_row = ' '.join(f"{value:.18e}" for value in row)
                file.write(formatted_row + "\n")



In [16]:
import numpy as np

def quat2mat(quat):
    """Convert quaternion to rotation matrix."""
    qw, qx, qy, qz = quat
    return np.array([
        [1 - 2*qy**2 - 2*qz**2, 2*qx*qy - 2*qz*qw, 2*qx*qz + 2*qy*qw],
        [2*qx*qy + 2*qz*qw, 1 - 2*qx**2 - 2*qz**2, 2*qy*qz - 2*qx*qw],
        [2*qx*qz - 2*qy*qw, 2*qy*qz + 2*qx*qw, 1 - 2*qx**2 - 2*qy**2]
    ])

def colmap_pose_to_arkit(R, T):
    """Convert a COLMAP world-to-camera pose to an ARKit camera-to-world pose."""
    R_inv = R.T  # Invert rotation
    T_inv = -R_inv @ T  # New translation

    # Construct the new 4x4 transformation matrix
    arkit_pose = np.eye(4)
    arkit_pose[:3, :3] = R_inv
    arkit_pose[:3, 3] = T_inv

    return arkit_pose

def process_poses(input_file, output_file,outputTrackNumberpose):
    with open(input_file, 'r') as file:
        lines = file.readlines()
    trackColors = []
    poses = []
    names=[]
    for line in lines:
        if line.startswith('#') or len(line.strip()) == 0:
            continue
        parts = line.split(' ')
        qw = float(parts[1])
        qx = float(parts[2])
        qy = float(parts[3])
        qz = float(parts[4])
        tx = float(parts[5])
        ty = float(parts[6])
        tz = float(parts[7])
        camera_id = parts[8].strip()
        name = parts[9].strip()
        name = name.split(".jpg")[0][-6:]
        trackColors.append(int(name))
        R = quat2mat([qw, qx, qy, qz])
        T = np.array([tx, ty, tz])
        
        arkit_pose = colmap_pose_to_arkit(R, T)
        poses.append(arkit_pose)
        names.append(name)
    with open(output_file, 'w') as file:
        for pose in poses:
            for row in pose:  
                formatted_row = ' '.join(f"{value:.18e}" for value in row)
                file.write(formatted_row + "\n")
            file.write("\n\n")
    with open(outputTrackNumberpose, 'w') as file:
        for name in names:
            file.write(name + "\n")
    with open(output_file_path, 'r') as file:
        lines = file.readlines()
# Example usage
for scene in glob.glob('/home/rozenberszki/D_Project/wsnsl/Datasets/data/*/iphone/colmap/images.txt'):
    scene_id = scene.split('/')[-4]
    output_file_path = f'/home/rozenberszki/D_Project/wsnsl/Dataset/{scene_id}/pose.txt'
    outputTrackNumberpose=f'/home/rozenberszki/D_Project/wsnsl/Dataset/{scene_id}/trackNumber.txt'
    process_poses(scene, output_file_path,outputTrackNumberpose)
'''
input_file_path = "/home/rozenberszki/D_Project/wsnsl/Datasets/data/56a0ec536c/iphone/colmap/images.txt" # Change this to your actual file path

output_file_path = '/home/rozenberszki/D_Project/wsnsl/Dataset/56a0ec536c/pose.txt'  # Change this to your desired output file path
outputTrackNumberpose='/home/rozenberszki/D_Project/wsnsl/Dataset/56a0ec536c/trackNumber.txt
'''
#process_poses(input_file_path, output_file_path,outputTrackNumberpose)


'\ninput_file_path = "/home/rozenberszki/D_Project/wsnsl/Datasets/data/56a0ec536c/iphone/colmap/images.txt" # Change this to your actual file path\n\noutput_file_path = \'/home/rozenberszki/D_Project/wsnsl/Dataset/56a0ec536c/pose.txt\'  # Change this to your desired output file path\noutputTrackNumberpose=\'/home/rozenberszki/D_Project/wsnsl/Dataset/56a0ec536c/trackNumber.txt\n'

In [17]:

'''# Paths to your JSON input and text output files
input_json_path = '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/pose_intrinsic_imu.json'  # Change this to the path of your JSON file
output_txt_path = '/home/rozenberszki/D_Project/wsnsl/Dataset/traj.txt'  # Change this to your desired output file path

# Read the data from JSON
pose_data = read_poses_from_json(input_json_path)

# Write the matrices to a text file
write_matrices_to_txt(pose_data, output_txt_path)
input_json_path = '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/pose_intrinsic_imu.json'  # Change this to the path of your JSON file'''
for path in os.listdir("Datasets/data"):
    print(path)
    temp=os.path.join("Datasets/data", path,"iphone/pose_intrinsic_imu.json")
    pose_data = read_poses_from_json(temp)
    output_txt_path = os.path.join('/home/rozenberszki/D_Project/wsnsl/Dataset',path)
    print(output_txt_path)
    os.makedirs(os.path.dirname(output_txt_path), exist_ok=True)
    print(output_txt_path)
    write_matrices_to_txt(pose_data,os.path.join( output_txt_path,"traj.txt"))
'''
pose_data = read_poses_from_json(input_json_path)
output_txt_path = '/home/rozenberszki/D_Project/wsnsl/Dataset/intrinsic.txt'
# Write the matrices to a text file
write_intirinsic_to_txt(pose_data, output_txt_path)
'''

8d563fc2cc
/home/rozenberszki/D_Project/wsnsl/Dataset/8d563fc2cc
/home/rozenberszki/D_Project/wsnsl/Dataset/8d563fc2cc
1841a0b525
/home/rozenberszki/D_Project/wsnsl/Dataset/1841a0b525
/home/rozenberszki/D_Project/wsnsl/Dataset/1841a0b525
8b5caf3398
/home/rozenberszki/D_Project/wsnsl/Dataset/8b5caf3398
/home/rozenberszki/D_Project/wsnsl/Dataset/8b5caf3398
75d29d69b8
/home/rozenberszki/D_Project/wsnsl/Dataset/75d29d69b8
/home/rozenberszki/D_Project/wsnsl/Dataset/75d29d69b8
07f5b601ee
/home/rozenberszki/D_Project/wsnsl/Dataset/07f5b601ee
/home/rozenberszki/D_Project/wsnsl/Dataset/07f5b601ee
b20a261fdf
/home/rozenberszki/D_Project/wsnsl/Dataset/b20a261fdf
/home/rozenberszki/D_Project/wsnsl/Dataset/b20a261fdf
7cd2ac43b4
/home/rozenberszki/D_Project/wsnsl/Dataset/7cd2ac43b4
/home/rozenberszki/D_Project/wsnsl/Dataset/7cd2ac43b4
c413b34238
/home/rozenberszki/D_Project/wsnsl/Dataset/c413b34238
/home/rozenberszki/D_Project/wsnsl/Dataset/c413b34238
56a0ec536c
/home/rozenberszki/D_Project/wsnsl/Da

"\npose_data = read_poses_from_json(input_json_path)\noutput_txt_path = '/home/rozenberszki/D_Project/wsnsl/Dataset/intrinsic.txt'\n# Write the matrices to a text file\nwrite_intirinsic_to_txt(pose_data, output_txt_path)\n"

In [3]:
import torch.nn.functional as F
def readDepth(filepath):
    depth = cv2.imread(filepath, cv2.IMREAD_UNCHANGED)
    depth_data = depth.astype(np.float32)
    depth_data = torch.from_numpy(depth_data)
    #print(depth_data.shape)
    #print(depth_data[0,0])
    return depth_data

In [19]:

color_paths = sorted(glob.glob(f"/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/*.jpg"))
print(color_paths)

color_data = cv2.imread(color_paths[0])
image = cv2.cvtColor(color_data, cv2.COLOR_BGR2RGB)

depth_paths = sorted(glob.glob(f"/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/processedData/depth/*.png"))
print("image",image.shape)
print("DEPT",readDepth(depth_paths[0]).shape)
print(readDepth(depth_paths[0])[0][0])

['/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000000.jpg', '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000001.jpg', '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000002.jpg', '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000003.jpg', '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000004.jpg', '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000005.jpg', '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000006.jpg', '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000007.jpg', '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000008.jpg', '/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/frame_000009.jpg', '/home/ro

In [24]:
import glob
from tqdm import tqdm  # Import tqdm

def readColorImage(filepath):
    # Read color image and convert to RGB (OpenCV uses BGR by default)
    image = cv2.imread(filepath, cv2.IMREAD_COLOR)
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    # Convert to float32 and normalize to [0, 1] if needed
    return torch.from_numpy(image.astype(np.float32) / 255.0)

def save_depth_image(input_path, output_filepath,amount=0, upscale=1):
    """Saves the depth image to a file."""
    depth_paths = sorted(
            glob.glob(os.path.join(input_path, "*.png"))
        )
    #print(depth_paths)
    os.makedirs(output_filepath, exist_ok=True)  # Ensure output path exists
    depth_paths=depth_paths[:amount]
    for i, depth_path in enumerate(tqdm(depth_paths, desc='Upsampling depth images')):
        # this changes the vals
        depth_data=readDepth(depth_path)#*1000
        # this image shape
        upsampled_depth_bilinear = F.interpolate(depth_data.unsqueeze(0).unsqueeze(0), 
                                                scale_factor=upscale, 
                                                mode='nearest', 
                                               ).squeeze()
        #print(upsampled_depth_bilinear.shape)
        upsampled_depth_bilinear = upsampled_depth_bilinear
        #upsampled_depth = upsampled_depth_bilinear * 6553.5
        upsampled_depth = upsampled_depth_bilinear.numpy().astype(np.uint16)
        #print((upsampled_depth.shape))

        cv2.imwrite(os.path.join(output_filepath, f"frame_{str(i).zfill(6)}.png"), upsampled_depth)
        
#bilateral filter
def save_color_image(input_path, output_filepath, amount=0, upscale=1):
    """Saves the color images to a file after upscaling."""
    color_paths = sorted(glob.glob(os.path.join(input_path, "*.jpg")))
    color_paths = color_paths[:amount] if amount > 0 else color_paths
    
    os.makedirs(output_filepath, exist_ok=True)  # Ensure output path exists
    
    for i, color_path in enumerate(tqdm(color_paths, desc='Processing color images')):
        color_data = readColorImage(color_path)
        color_data = color_data.permute(2, 0, 1).unsqueeze(0)  # CxHxW and add batch dimension
        
        upsampled_color_bilinear = F.interpolate(color_data, 
                                                scale_factor=upscale, 
                                                mode='nearest', 
                                                ).squeeze(0)
        
        # Convert back to uint8 and BGR for saving
        upsampled_color = (upsampled_color_bilinear.permute(1, 2, 0) * 255).byte().numpy()
        upsampled_color = cv2.cvtColor(upsampled_color, cv2.COLOR_RGB2BGR)
        #print(upsampled_color.shape)
        cv2.imwrite(os.path.join(output_filepath, f"frame_{str(i).zfill(6)}.jpg"), upsampled_color)

#mylist=["f8f12e4e6b", "e9ac2fc517","0b031f3119", "40b56bf310","e3ecd49e2b", "9f139a318d", "419cbe7c11","5fb5d2dbf2","8b5caf3398","41b00feddb","98b4ec142f","b20a261fdf","fe1733741f","7cd2ac43b4","8d563fc2cc","39f36da05b","8b5caf3398","b20a261fdf","fe1733741f","07f5b601ee","75d29d69b8"]
for path in os.listdir("Datasets/data"):
    if path=="56a0ec536c":
        continue
    amount=glob.glob(os.path.join('/home/rozenberszki/D_Project/wsnsl/Datasets/data',path, "iphone/rgb", "*.jpg"))
    print(amount)
    amount=len(amount)
    print(amount)
    temp=os.path.join("Datasets/data", path,"iphone/pose_intrinsic_imu.json")
    pose_data = read_poses_from_json(temp)
    output_txt_path = os.path.join('/home/rozenberszki/D_Project/wsnsl/Dataset',path)
    os.makedirs(os.path.dirname(output_txt_path), exist_ok=True)

    write_matrices_to_txt(pose_data,os.path.join( output_txt_path,"traj.txt"))

    save_color_image(os.path.join('Datasets/data',path, "iphone/rgb"), os.path.join('/home/rozenberszki/D_Project/wsnsl/Dataset/', path, "color_path/"),amount=amount,upscale=0.333334)
    save_depth_image(os.path.join('Datasets/data',path, "iphone/depth"), os.path.join('/home/rozenberszki/D_Project/wsnsl/Dataset/', path, "color_path/"),amount=amount,upscale=2.5)

#save_color_image('/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/rgb/', '/home/rozenberszki/D_Project/wsnsl/Dataset/color_path/',amount=2000,upscale=0.333334)
#save_depth_image('/home/rozenberszki/project/wsnsl/Datasets/Scannet++/data/56a0ec536c/iphone/depth', '/home/rozenberszki/D_Project/wsnsl/Dataset/color_path/',amount=2000,upscale=2.5)
#save_depth_image('/home/rozenberszki/D_Project/wsnsl/Dataset/depth_rendered/56a0ec536c/iphone/render_depth', '/home/rozenberszki/D_Project/wsnsl/Dataset/renderedDepthScaled/',amount=946,upscale=0.333334)
#0.5, 3.75'

['/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_000885.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_003441.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_005883.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_003659.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_004554.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_006153.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_003137.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_007001.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_004843.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_002376.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8d563fc2cc/iphone/rgb/frame_007154.jpg'

Upsampling depth images: 100%|██████████| 7237/7237 [00:43<00:00, 165.76it/s]


['/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_000885.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_003441.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_005883.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_008089.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_003659.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_004554.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_006153.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_003137.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_007001.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_004843.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/1841a0b525/iphone/rgb/frame_002376.jpg'

Upsampling depth images: 100%|██████████| 8423/8423 [00:51<00:00, 164.85it/s]


['/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_000885.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_003441.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_005883.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_003659.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_004554.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_006153.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_003137.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_007001.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_004843.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_002376.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/8b5caf3398/iphone/rgb/frame_007154.jpg'

...

Upsampling depth images: 100%|██████████| 7896/7896 [00:46<00:00, 170.02it/s]


['/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_000885.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_003441.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_005883.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_008089.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_003659.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_004554.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_006153.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_003137.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_007001.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_004843.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/39f36da05b/iphone/rgb/frame_002376.jpg'

Upsampling depth images: 100%|██████████| 9867/9867 [00:59<00:00, 164.57it/s]


['/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_000885.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_003441.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_005883.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_008089.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_003659.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_004554.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_006153.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_003137.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_010478.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_007001.jpg', '/home/rozenberszki/D_Project/wsnsl/Datasets/data/fe1733741f/iphone/rgb/frame_011273.jpg'

Upsampling depth images: 100%|██████████| 11684/11684 [01:12<00:00, 160.60it/s]


In [13]:

def realWorldProject(uv, Tf, K, depthf):
    K_inv = np.array(
        [
            [1 / K[0, 0], 0.0, -K[0, 2] / K[0, 0]],
            [0.0, 1 / K[1, 1], -K[1, 2] / K[1, 1]],
            [0.0, 0.0, 1.0],
        ]
    )

    tmp = np.concatenate([uv, np.ones((1, uv.shape[1]))])
    tmp = K_inv @ tmp
    if isinstance(uv, np.ndarray):
        tmp = tmp * depthf[uv[1].astype(np.int64), uv[0].astype(np.int64)].numpy()
    else:
        tmp = (
            tmp * depthf[uv[1].long(), uv[0].long()].numpy()
        )  # real world in camera coordinates
    tmp = np.concatenate([tmp, np.ones((1, tmp.shape[1]))])
    tmp = Tf @ tmp  # real world coordinates
    tmp = tmp[:3, :]  # real world coordinates

    return tmp
''' H: 480 #480 # 720
  W: 640 #680 920
  fx: 476.333 #480
  fy: 476.333 #480
  cx: 318 # 318
  cy: 240 #  240'''

K = np.array([[577.590698, 0.000000, 318.905426], [0.000000, 578.729797, 242.683609], [0.000000, 0.000000, 1.000000]])

In [14]:
import glob
import numpy as np

In [17]:
import yaml
from tqdm import tqdm

def modify_config(template, unique_id,asList):
    # Replace placeholders in the template with the unique identifier.
    template['data']['input_folder'] = f"Datasets/ScanNet_orig/{unique_id}"
    template['data']['output'] = f"output/ScanNet_orig/{unique_id}"
    template['data']['logs'] = f"logs/ScanNet_orig/{unique_id}"
    template['mapping']['bound']  = '[' + ', '.join(['[' + ', '.join(map(str, row)) + ']' for row in asList]) + ']'
    template['mapping']['marching_cubes_bound'] =  '[' + ', '.join(['[' + ', '.join(map(str, row)) + ']' for row in asList]) + ']'
    
    return template

def create_yaml_file(config, filename):
    # Write the configuration to a YAML file.
    full_filename = f"/home/rozenberszki/project/wsnsl/configs/ScanNet_orig/{filename}.yaml"
    with open(full_filename, 'w') as file:
        yaml.dump(config, file, default_flow_style=False)

# Load the base configuration from a YAML file (assuming it is named 'base_config.yaml')
with open("/home/rozenberszki/project/wsnsl/configs/ScanNet_orig/scene0131_01.yaml", 'r') as file:
    base_config = yaml.safe_load(file)


#numbering = len(np.loadtxt(open(os.path.join('/home/rozenberszki/D_Project/wsnsl/Dataset',"56a0ec536c", "trackNumber.txt"))).flatten())
sorted(glob.glob('/home/rozenberszki/project/wsnsl/Datasets/ScanNet_orig/pose/*'), key=lambda x: int(x.split('/')[-1].split('.')[0]))
for path in os.listdir('/home/rozenberszki/project/wsnsl/Datasets/ScanNet_orig'):
    print(path)
    # for loop
    
    paths = sorted(glob.glob(f'/home/rozenberszki/project/wsnsl/Datasets/ScanNet_orig/{path}/pose_5/*'), key=lambda x: int(x.split('/')[-1].split('.')[0]))
    poses = np.stack([np.loadtxt(path) for path in paths])
    #poses = np.loadtxt(os.path.join('/home/rozenberszki/project/wsnsl/Datasets/ScanNet_orig',path,'pose.txt')).reshape(-1, 4, 4)
    #poses.shape
    directory_path = os.path.join('/home/rozenberszki/project/wsnsl/Datasets/ScanNet_orig',path,'color_5')

    # Retrieve and sort all PNG files numerically by the number in their filename
    depths = sorted(
        glob.glob(os.path.join('/home/rozenberszki/project/wsnsl/Datasets/ScanNet_orig',path,'depth_5' ,'*.png')), 
        key=lambda x: int(x.split('/')[-1].split('.')[0])
    )

    # Display sorted file paths
    png_depth_scale = 1000
    depth_data = cv2.imread(depths[0], cv2.IMREAD_UNCHANGED)
    depth_data = depth_data.astype(np.float32) / png_depth_scale
    depth = np.array(depth_data)
    out = realWorldProject(np.array(np.where(depth > 0))[::-1], poses[0], K, torch.from_numpy(depth))
    temp= out[0:3, :]

    ''' numbering = len(np.loadtxt(open(os.path.join('/home/rozenberszki/D_Project/wsnsl/Dataset',path, "trackNumber.txt"))).flatten()) '''    
    for i in tqdm(range(0,len(depths),10)):
        out = realWorldProject(np.array(np.where(depth > 0))[::-1], poses[i], K, torch.from_numpy(depth))
        temp = np.concatenate((temp, out[0:3, :]), axis=1)

    out_min = np.min(temp, axis=1)
    out_max = np.max(temp, axis=1)
    output=list(zip(out_min, out_max))
    asList=[]
    for i in output:
        asList.append(list(i))
    modified_config = modify_config(base_config.copy(), path, asList)
    create_yaml_file(modified_config, path)
    print(f"Created {path}.yaml")


scene0131_01


100%|██████████| 23/23 [00:00<00:00, 32.00it/s]


Created scene0131_01.yaml
scene0025_00


100%|██████████| 39/39 [00:02<00:00, 14.50it/s]


Created scene0025_00.yaml
scene0671_00


...

Created scene0671_00.yaml
scene0011_00


100%|██████████| 48/48 [00:02<00:00, 23.92it/s]


Created scene0011_00.yaml
scene0046_00


100%|██████████| 50/50 [00:03<00:00, 16.66it/s]


Created scene0046_00.yaml


In [23]:

color_paths = sorted(glob.glob(f"/home/rozenberszki/D_Project/wsnsl/Dataset/color_path/*.jpg"))
print(color_paths)

color_data = cv2.imread(color_paths[0])
image = cv2.cvtColor(color_data, cv2.COLOR_BGR2RGB)

depth_paths = sorted(glob.glob(f"/home/rozenberszki/D_Project/wsnsl/Dataset/color_path/*.png"))
print("image",image.shape)
print("DEPT",readDepth(depth_paths[0]).shape)
print(readDepth(depth_paths[0])[0][0])


[]


IndexError: list index out of range

np.linalg.inv(pose_data_temp[0])